In [1]:
import numpy as np
import pandas as pd
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
import json
!conda install -c conda-forge geopy --yes
from geopy.geocoders import Nominatim
import requests
from pandas.io.json import json_normalize
import matplotlib.cm as cm
import matplotlib.colors as colors
from sklearn.cluster import KMeans
!conda install -c conda-forge folium=0.5.0 --yes
import folium
print('Libraries imported.')

Solving environment: done

## Package Plan ##

  environment location: /opt/conda/envs/Python36

  added / updated specs: 
    - geopy


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    geopy-1.20.0               |             py_0          57 KB  conda-forge
    ca-certificates-2019.9.11  |       hecc5488_0         144 KB  conda-forge
    geographiclib-1.50         |             py_0          34 KB  conda-forge
    openssl-1.1.1d             |       h516909a_0         2.1 MB  conda-forge
    certifi-2019.9.11          |           py36_0         147 KB  conda-forge
    ------------------------------------------------------------
                                           Total:         2.5 MB

The following NEW packages will be INSTALLED:

    geographiclib:   1.50-py_0         conda-forge
    geopy:           1.20.0-py_0       conda-forge

The following packages will be UPDATED:

    cer

In [2]:
from bs4 import BeautifulSoup
import urllib
import urllib.request

In [3]:
!wget -q -O 'newyork_data.json' https://cocl.us/new_york_dataset
print('Data downloaded!')

Data downloaded!


In [4]:
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

In [5]:
newyork_data

{'type': 'FeatureCollection',
 'totalFeatures': 306,
 'features': [{'type': 'Feature',
   'id': 'nyu_2451_34572.1',
   'geometry': {'type': 'Point',
    'coordinates': [-73.84720052054902, 40.89470517661]},
   'geometry_name': 'geom',
   'properties': {'name': 'Wakefield',
    'stacked': 1,
    'annoline1': 'Wakefield',
    'annoline2': None,
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.84720052054902,
     40.89470517661,
     -73.84720052054902,
     40.89470517661]}},
  {'type': 'Feature',
   'id': 'nyu_2451_34572.2',
   'geometry': {'type': 'Point',
    'coordinates': [-73.82993910812398, 40.87429419303012]},
   'geometry_name': 'geom',
   'properties': {'name': 'Co-op City',
    'stacked': 2,
    'annoline1': 'Co-op',
    'annoline2': 'City',
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.82993910812398,
     40.87429419303012,
     -73.82993910812398,
     40.87429419303012]}},
  {'type': 'Feature',
 

In [6]:
neighborhoods_data = newyork_data['features']

In [7]:
neighborhoods_data[0]

{'type': 'Feature',
 'id': 'nyu_2451_34572.1',
 'geometry': {'type': 'Point',
  'coordinates': [-73.84720052054902, 40.89470517661]},
 'geometry_name': 'geom',
 'properties': {'name': 'Wakefield',
  'stacked': 1,
  'annoline1': 'Wakefield',
  'annoline2': None,
  'annoline3': None,
  'annoangle': 0.0,
  'borough': 'Bronx',
  'bbox': [-73.84720052054902,
   40.89470517661,
   -73.84720052054902,
   40.89470517661]}}

In [8]:
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude']
neighborhoods = pd.DataFrame(columns=column_names)

In [9]:
neighborhoods

Empty DataFrame
Columns: [Borough, Neighborhood, Latitude, Longitude]
Index: []

In [10]:
for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

In [11]:
neighborhoods.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

In [12]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(neighborhoods['Borough'].unique()),
        neighborhoods.shape[0]
    )
)

The dataframe has 5 boroughs and 306 neighborhoods.


In [13]:
address = 'New York City, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of New York City are 40.7127281, -74.0060152.


In [14]:
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

In [15]:
newyork_data = neighborhoods
newyork_data.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

In [16]:
CLIENT_ID = 'E5KVN2UWQURTJMYS3ZFOJDUYA3IV3PGB3ELPVRGRIV4UDODD'
CLIENT_SECRET = 'CYN0UAZQU2XCNFCG0QJUOXBM5HXVDN0F2YP0EQXKU4KINESA'
VERSION = '20180605'

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: E5KVN2UWQURTJMYS3ZFOJDUYA3IV3PGB3ELPVRGRIV4UDODD
CLIENT_SECRET:CYN0UAZQU2XCNFCG0QJUOXBM5HXVDN0F2YP0EQXKU4KINESA


In [17]:
newyork_data.loc[0, 'Neighborhood']

'Wakefield'

In [18]:
neighborhood_latitude = newyork_data.loc[0, 'Latitude']
neighborhood_longitude = newyork_data.loc[0, 'Longitude']

neighborhood_name = newyork_data.loc[0, 'Neighborhood']

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))

Latitude and longitude values of Wakefield are 40.89470517661, -73.84720052054902.


In [19]:
LIMIT = 100
radius = 500
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)
url

'https://api.foursquare.com/v2/venues/explore?&client_id=E5KVN2UWQURTJMYS3ZFOJDUYA3IV3PGB3ELPVRGRIV4UDODD&client_secret=CYN0UAZQU2XCNFCG0QJUOXBM5HXVDN0F2YP0EQXKU4KINESA&v=20180605&ll=40.89470517661,-73.84720052054902&radius=500&limit=100'

In [20]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5dc59d02be7078002c2b72d0'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': 'Open now', 'key': 'openNow'}]},
  'headerLocation': 'Wakefield',
  'headerFullLocation': 'Wakefield, Bronx',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 9,
  'suggestedBounds': {'ne': {'lat': 40.899205181110005,
    'lng': -73.84125857127495},
   'sw': {'lat': 40.89020517211, 'lng': -73.8531424698231}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4c537892fd2ea593cb077a28',
       'name': 'Lollipops Gelato',
       'location': {'address': '4120 Baychester Ave',
        'crossStreet': 'Edenwald & Bussing Ave',
        'lat': 40.894123150205274,
        'lng': -73.84589162362325,
        'labeledLatLn

In [21]:
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [22]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues)

filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

name      categories        lat        lng
0  Lollipops Gelato    Dessert Shop  40.894123 -73.845892
1          Rite Aid        Pharmacy  40.896649 -73.844846
2  Carvel Ice Cream  Ice Cream Shop  40.890487 -73.848568
3             Shell     Gas Station  40.894187 -73.845862
4           Dunkin'      Donut Shop  40.890459 -73.849089

In [23]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

9 venues were returned by Foursquare.


In [24]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [25]:
newyork_venues = getNearbyVenues(names=newyork_data['Neighborhood'],
                                   latitudes=newyork_data['Latitude'],
                                   longitudes=newyork_data['Longitude']
                                  )

Wakefield
Co-op City
Eastchester
Fieldston
Riverdale
Kingsbridge
Marble Hill
Woodlawn
Norwood
Williamsbridge
Baychester
Pelham Parkway
City Island
Bedford Park
University Heights
Morris Heights
Fordham
East Tremont
West Farms
High  Bridge
Melrose
Mott Haven
Port Morris
Longwood
Hunts Point
Morrisania
Soundview
Clason Point
Throgs Neck
Country Club
Parkchester
Westchester Square
Van Nest
Morris Park
Belmont
Spuyten Duyvil
North Riverdale
Pelham Bay
Schuylerville
Edgewater Park
Castle Hill
Olinville
Pelham Gardens
Concourse
Unionport
Edenwald
Bay Ridge
Bensonhurst
Sunset Park
Greenpoint
Gravesend
Brighton Beach
Sheepshead Bay
Manhattan Terrace
Flatbush
Crown Heights
East Flatbush
Kensington
Windsor Terrace
Prospect Heights
Brownsville
Williamsburg
Bushwick
Bedford Stuyvesant
Brooklyn Heights
Cobble Hill
Carroll Gardens
Red Hook
Gowanus
Fort Greene
Park Slope
Cypress Hills
East New York
Starrett City
Canarsie
Flatlands
Mill Island
Manhattan Beach
Coney Island
Bath Beach
Borough Park
Dyker

In [26]:
print(newyork_venues.shape)
newyork_venues.head()

(10264, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0    Wakefield              40.894705              -73.847201   
1    Wakefield              40.894705              -73.847201   
2    Wakefield              40.894705              -73.847201   
3    Wakefield              40.894705              -73.847201   
4    Wakefield              40.894705              -73.847201   

              Venue  Venue Latitude  Venue Longitude  Venue Category  
0  Lollipops Gelato       40.894123       -73.845892    Dessert Shop  
1          Rite Aid       40.896649       -73.844846        Pharmacy  
2  Carvel Ice Cream       40.890487       -73.848568  Ice Cream Shop  
3             Shell       40.894187       -73.845862     Gas Station  
4           Dunkin'       40.890459       -73.849089      Donut Shop

In [27]:
newyork_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  \
Neighborhood                                                               
Allerton                                      30                      30   
Annadale                                      13                      13   
Arden Heights                                  6                       6   
Arlington                                      4                       4   
Arrochar                                      17                      17   
Arverne                                       19                      19   
Astoria                                      100                     100   
Astoria Heights                               13                      13   
Auburndale                                    20                      20   
Bath Beach                                    44                      44   
Battery Park City                             99                      99   
Bay Ridge                                     89                      89   
Bay Terrace                                   48                      48   
Baychester                                    23                      23   
Bayside                                       72                      72   
Bayswater                                      2                       2   
Bedford Park                                  34                      34   
Bedford Stuyvesant                            27                      27   
Beechhurst                                    14                      14   
Bellaire                                      12                      12   
Belle Harbor                                  17                      17   
Bellerose                                     22                      22   
Belmont                                      100                     100   
Bensonhurst                                   34                      34   
Bergen Beach                                   8                       8   
Blissville                                    21                      21   
Bloomfield                                     5                       5   
Boerum Hill                                   84                      84   
Borough Park                                  23                      23   
Breezy Point                                   4                       4   
Briarwood                                      9                       9   
Brighton Beach                                43                      43   
Broad Channel                                  5                       5   
Broadway Junction                             13                      13   
Bronxdale                                     15                      15   
Brooklyn Heights                             100                     100   
Brookville                                     1                       1   
Brownsville                                   18                      18   
Bulls Head                                    42                      42   
Bushwick                                      74                      74   
Butler Manor                                   5                       5   
Cambria Heights                               13                      13   
Canarsie                                       7                       7   
Carnegie Hill                                100                     100   
Carroll Gardens                              100                     100   
Castle Hill                                    7                       7   
Castleton Corners                             13                      13   
Central Harlem                                46                      46   
Charleston                                    31                      31   
Chelsea                                      105                     105   
Chinatown                                    100                     100   

In [28]:
print('There are {} uniques categories.'.format(len(newyork_venues['Venue Category'].unique())))

There are 434 uniques categories.


In [29]:
newyork_onehot = pd.get_dummies(newyork_venues[['Venue Category']], prefix="", prefix_sep="")

newyork_onehot['Neighborhood'] = newyork_venues['Neighborhood'] 

fixed_columns = [newyork_onehot.columns[-1]] + list(newyork_onehot.columns[:-1])
newyork_onehot = newyork_onehot[fixed_columns]

newyork_onehot.head()

Yoga Studio  ATM  Accessories Store  Adult Boutique  Afghan Restaurant  \
0            0    0                  0               0                  0   
1            0    0                  0               0                  0   
2            0    0                  0               0                  0   
3            0    0                  0               0                  0   
4            0    0                  0               0                  0   

   African Restaurant  American Restaurant  Animal Shelter  Antique Shop  \
0                   0                    0               0             0   
1                   0                    0               0             0   
2                   0                    0               0             0   
3                   0                    0               0             0   
4                   0                    0               0             0   

   Arcade  Arepa Restaurant  Argentinian Restaurant  Art Gallery  Art Museum  \
0       0                 0                       0            0           0   
1       0                 0                       0            0           0   
2       0                 0                       0            0           0   
3       0                 0                       0            0           0   
4       0                 0                       0            0           0   

   Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  \
0                    0                     0                 0   
1                    0                     0                 0   
2                    0                     0                 0   
3                    0                     0                 0   
4                    0                     0                 0   

   Athletics & Sports  Auditorium  Australian Restaurant  Austrian Restaurant  \
0                   0           0                      0                    0   
1                   0           0                      0                    0   
2                   0           0                      0                    0   
3                   0           0                      0                    0   
4                   0           0                      0                    0   

   Auto Garage  Auto Workshop  Automotive Shop  BBQ Joint  Baby Store  \
0            0              0                0          0           0   
1            0              0                0          0           0   
2            0              0                0          0           0   
3            0              0                0          0           0   
4            0              0                0          0           0   

   Bagel Shop  Bakery  Bank  Bar  Baseball Field  Baseball Stadium  \
0           0       0     0    0               0                 0   
1           0       0     0    0               0                 0   
2           0       0     0    0               0                 0   
3           0       0     0    0               0                 0   
4           0       0     0    0               0                 0   

   Basketball Court  Bath House  Beach  Beach Bar  Bed & Breakfast  Beer Bar  \
0                 0           0      0          0                0         0   
1                 0           0      0          0                0         0   
2                 0           0      0          0                0         0   
3                 0           0      0          0                0         0   
4                 0           0      0          0                0         0   

   Beer Garden  Beer Store  Big Box Store  Bike Rental / Bike Share  \
0            0           0              0                         0   
1            0           0              0                         0   
2            0           0              0                         0   
3            0           0              0                         0   
4            0        

In [30]:
newyork_onehot.shape

(10264, 434)

In [31]:
newyork_grouped = newyork_onehot.groupby('Neighborhood').mean().reset_index()
newyork_grouped

Neighborhood  Yoga Studio       ATM  Accessories Store  \
0                     Allerton     0.000000  0.000000           0.000000   
1                     Annadale     0.000000  0.000000           0.000000   
2                Arden Heights     0.000000  0.000000           0.000000   
3                    Arlington     0.000000  0.000000           0.000000   
4                     Arrochar     0.000000  0.000000           0.000000   
5                      Arverne     0.000000  0.000000           0.000000   
6                      Astoria     0.000000  0.000000           0.000000   
7              Astoria Heights     0.000000  0.000000           0.000000   
8                   Auburndale     0.000000  0.000000           0.000000   
9                   Bath Beach     0.000000  0.000000           0.000000   
10           Battery Park City     0.000000  0.000000           0.000000   
11                   Bay Ridge     0.000000  0.000000           0.000000   
12                 Bay Terrace     0.000000  0.000000           0.020833   
13                  Baychester     0.000000  0.000000           0.000000   
14                     Bayside     0.013889  0.000000           0.000000   
15                   Bayswater     0.000000  0.000000           0.000000   
16                Bedford Park     0.000000  0.000000           0.000000   
17          Bedford Stuyvesant     0.000000  0.000000           0.000000   
18                  Beechhurst     0.071429  0.000000           0.000000   
19                    Bellaire     0.000000  0.000000           0.000000   
20                Belle Harbor     0.000000  0.000000           0.000000   
21                   Bellerose     0.000000  0.000000           0.000000   
22                     Belmont     0.000000  0.000000           0.000000   
23                 Bensonhurst     0.000000  0.000000           0.000000   
24                Bergen Beach     0.000000  0.000000           0.000000   
25                  Blissville     0.000000  0.000000           0.000000   
26                  Bloomfield     0.000000  0.000000           0.000000   
27                 Boerum Hill     0.023810  0.000000           0.000000   
28                Borough Park     0.000000  0.000000           0.000000   
29                Breezy Point     0.000000  0.000000           0.000000   
30                   Briarwood     0.000000  0.000000           0.000000   
31              Brighton Beach     0.000000  0.000000           0.000000   
32               Broad Channel     0.000000  0.000000           0.000000   
33           Broadway Junction     0.000000  0.000000           0.000000   
34                   Bronxdale     0.000000  0.000000           0.000000   
35            Brooklyn Heights     0.050000  0.000000           0.000000   
36                  Brookville     0.000000  0.000000           0.000000   
37                 Brownsville     0.000000  0.000000           0.000000   
38                  Bulls Head     0.000000  0.000000           0.000000   
39                    Bushwick     0.000000  0.000000           0.000000   
40                Butler Manor     0.000000  0.000000           0.000000   
41             Cambria Heights     0.000000  0.000000           0.000000   
42                    Canarsie     0.000000  0.000000           0.000000   
43               Carnegie Hill     0.030000  0.000000           0.000000   
44             Carroll Gardens     0.000000  0.000000           0.000000   
45                 Castle Hill     0.000000  0.000000           0.000000   
46           Castleton Corners     0.000000  0.000000           0.000000   
47              Central Harlem     0.000000  0.000000           0.000000   
48                  Charleston     0.000000  0.000000           0.000000   
49                     Chelsea     0.000000  0.000000           0.000000   
50                   Chinatown     0.000000  0.000000           0.000000   
51                 City Island     0.000000  0.000000           0.

In [32]:
newyork_grouped.shape

(301, 434)

In [33]:
num_top_venues = 5

for hood in newyork_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = newyork_grouped[newyork_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Allerton----
                venue  freq
0       Deli / Bodega  0.10
1         Pizza Place  0.10
2  Chinese Restaurant  0.10
3         Supermarket  0.10
4         Gas Station  0.03


----Annadale----
            venue  freq
0     Pizza Place  0.15
1    Dance Studio  0.08
2  Cosmetics Shop  0.08
3        Pharmacy  0.08
4   Train Station  0.08


----Arden Heights----
                 venue  freq
0  Rental Car Location  0.17
1        Deli / Bodega  0.17
2          Coffee Shop  0.17
3          Pizza Place  0.17
4             Bus Stop  0.17


----Arlington----
                 venue  freq
0  American Restaurant  0.25
1             Bus Stop  0.25
2        Boat or Ferry  0.25
3        Grocery Store  0.25
4          Yoga Studio  0.00


----Arrochar----
                      venue  freq
0             Deli / Bodega  0.12
1        Italian Restaurant  0.12
2                  Bus Stop  0.12
3  Mediterranean Restaurant  0.06
4               Supermarket  0.06


----Arverne----
            venue  

In [34]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [35]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = newyork_grouped['Neighborhood']

for ind in np.arange(newyork_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(newyork_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0       Allerton    Chinese Restaurant         Deli / Bodega   
1       Annadale           Pizza Place          Liquor Store   
2  Arden Heights           Pizza Place   Rental Car Location   
3      Arlington   American Restaurant         Grocery Store   
4       Arrochar              Bus Stop    Italian Restaurant   

  3rd Most Common Venue 4th Most Common Venue     5th Most Common Venue  \
0           Supermarket           Pizza Place                Donut Shop   
1   American Restaurant              Pharmacy                 Pet Store   
2         Deli / Bodega              Pharmacy               Coffee Shop   
3         Boat or Ferry              Bus Stop             Women's Store   
4         Deli / Bodega           Pizza Place  Mediterranean Restaurant   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0    Spanish Restaurant   Fried Chicken Joint           Bus Station   
1                 Diner            Restaurant                  Food   
2              Bus Stop  Fast Food Restaurant  Ethiopian Restaurant   
3   Filipino Restaurant           Event Space               Exhibit   
4            Food Truck        Cosmetics Shop    Athletics & Sports   

   9th Most Common Venue 10th Most Common Venue  
0            Gas Station   Fast Food Restaurant  
1           Dance Studio         Cosmetics Shop  
2          Event Service            Event Space  
3             Eye Doctor                Factory  
4  Outdoors & Recreation         Sandwich Place

In [36]:
kclusters = 5

newyork_grouped_clustering = newyork_grouped.drop('Neighborhood', 1)

kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(newyork_grouped_clustering)

kmeans.labels_[0:10] 

array([0, 0, 0, 2, 0, 0, 0, 0, 0, 0], dtype=int32)

In [37]:
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

newyork_merged = newyork_data

newyork_merged = newyork_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood', how='right')

newyork_merged.head()

Borough Neighborhood   Latitude  Longitude  Cluster Labels  \
0   Bronx    Wakefield  40.894705 -73.847201               0   
1   Bronx   Co-op City  40.874294 -73.829939               0   
2   Bronx  Eastchester  40.887556 -73.827806               0   
3   Bronx    Fieldston  40.895437 -73.905643               0   
4   Bronx    Riverdale  40.890834 -73.912585               0   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0              Pharmacy          Dessert Shop        Sandwich Place   
1           Bus Station  Fast Food Restaurant            Restaurant   
2           Bus Station  Caribbean Restaurant                 Diner   
3                 River           Bus Station                 Plaza   
4                  Park            Food Truck           Bus Station   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0  Caribbean Restaurant            Donut Shop        Ice Cream Shop   
1        Mattress Store                  Park         Grocery Store   
2              Bus Stop         Metro Station            Donut Shop   
3         Women's Store  Fast Food Restaurant    English Restaurant   
4        Baseball Field                   Gym          Home Service   

  7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0            Laundromat           Gas Station         Women's Store   
1              Pharmacy           Pizza Place        Discount Store   
2    Seafood Restaurant           Pizza Place              Platform   
3  Ethiopian Restaurant         Event Service           Event Space   
4                 Plaza                  Bank           Flea Market   

  10th Most Common Venue  
0     Falafel Restaurant  
1                    Bar  
2   Fast Food Restaurant  
3                Exhibit  
4            Fish Market

In [38]:
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

markers_colors = []
for lat, lon, poi, cluster in zip(newyork_merged['Latitude'], newyork_merged['Longitude'], newyork_merged['Neighborhood'], newyork_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [39]:
newyork_merged.loc[newyork_merged['Cluster Labels'] == 0, newyork_merged.columns[[1] + list(range(5, newyork_merged.shape[1]))]]

Neighborhood       1st Most Common Venue  \
0                    Wakefield                    Pharmacy   
1                   Co-op City                 Bus Station   
2                  Eastchester                 Bus Station   
3                    Fieldston                       River   
4                    Riverdale                        Park   
5                  Kingsbridge                 Pizza Place   
6                  Marble Hill                 Coffee Shop   
7                     Woodlawn               Deli / Bodega   
8                      Norwood                 Pizza Place   
9               Williamsbridge                  Soup Place   
10                  Baychester                  Donut Shop   
11              Pelham Parkway          Italian Restaurant   
12                 City Island             Harbor / Marina   
13                Bedford Park                       Diner   
14          University Heights                 Pizza Place   
15              Morris Heights                        Bank   
16                     Fordham                  Donut Shop   
17                East Tremont                 Pizza Place   
18                  West Farms                 Bus Station   
19                High  Bridge          Chinese Restaurant   
20                     Melrose                 Pizza Place   
21                  Mott Haven                  Donut Shop   
22                 Port Morris                         Bar   
23                    Longwood        Fast Food Restaurant   
24                 Hunts Point               Grocery Store   
25                  Morrisania              Discount Store   
26                   Soundview          Chinese Restaurant   
28                 Throgs Neck               Deli / Bodega   
29                Country Club              Sandwich Place   
30                 Parkchester                 Supermarket   
31          Westchester Square        Fast Food Restaurant   
32                    Van Nest                 Pizza Place   
33                 Morris Park                 Pizza Place   
34                     Belmont          Italian Restaurant   
35              Spuyten Duyvil                        Park   
36             North Riverdale                 Pizza Place   
37                  Pelham Bay                        Bank   
38               Schuylerville                    Pharmacy   
39              Edgewater Park          Italian Restaurant   
40                 Castle Hill                      Market   
41                   Olinville        Caribbean Restaurant   
42              Pelham Gardens          Chinese Restaurant   
43                   Concourse                      Bakery   
44                   Unionport   Latin American Restaurant   
45                    Edenwald                 Supermarket   
46                   Bay Ridge          Italian Restaurant   
47                 Bensonhurst                 Pizza Place   
48                 Sunset Park                        Bank   
49                  Greenpoint                         Bar   
50                   Gravesend                 Pizza Place   
51              Brighton Beach          Russian Restaurant   
52              Sheepshead Bay          Turkish Restaurant   
53           Manhattan Terrace                 Pizza Place   
54                    Flatbush        Caribbean Restaurant   
55               Crown Heights                 Pizza Place   
56               East Flatbush                        Park   
57                  Kensington             Thai Restaurant   
58             Windsor Terrace               Grocery Store   
59            Prospect Heights                         Bar   
60                 Brownsville               Moving Target   
61                Williamsburg                 Coffee Shop   
62                    Bushwick                         Bar   
63          Bedford Stuyvesant                 Coffee Shop   
64            Brooklyn Heights                 Yog

In [40]:
newyork_merged.loc[newyork_merged['Cluster Labels'] == 1, newyork_merged.columns[[1] + list(range(5, newyork_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
192   Somerville                  Park         Women's Store   
203    Todt Hill                  Park         Women's Store   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
192                 Field  Ethiopian Restaurant         Event Service   
203                 Field  Ethiopian Restaurant         Event Service   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
192           Event Space               Exhibit            Eye Doctor   
203           Event Space               Exhibit            Eye Doctor   

    9th Most Common Venue 10th Most Common Venue  
192               Factory     Falafel Restaurant  
203               Factory     Falafel Restaurant

In [41]:
newyork_merged.loc[newyork_merged['Cluster Labels'] == 2, newyork_merged.columns[[1] + list(range(5, newyork_merged.shape[1]))]]

Neighborhood 1st Most Common Venue      2nd Most Common Venue  \
27    Clason Point                  Park  South American Restaurant   
193     Brookville         Deli / Bodega              Women's Store   
198   New Brighton              Bus Stop                       Park   
202    Grymes Hill               Dog Run                   Bus Stop   
204    South Beach                  Pier                      Beach   
224      Park Hill              Bus Stop         Athletics & Sports   
226   Graniteville              Bus Stop                 Food Truck   
227      Arlington   American Restaurant              Grocery Store   
245     Bloomfield     Recreation Center                   Bus Stop   
254        Concord  Gym / Fitness Center        Peruvian Restaurant   
256  Randall Manor                  Park                 Bagel Shop   
285    Willowbrook              Bus Stop              Deli / Bodega   
303      Bayswater            Playground                       Park   
305      Fox Hills         Deli / Bodega              Grocery Store   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
27           Home Service         Grocery Store                  Pool   
193   Filipino Restaurant  Ethiopian Restaurant         Event Service   
198         Deli / Bodega         Bowling Alley     Convenience Store   
202         Women's Store   Filipino Restaurant         Event Service   
204         Deli / Bodega              Bus Stop    Athletics & Sports   
224  Gym / Fitness Center           Coffee Shop                 Hotel   
226           Supermarket   Filipino Restaurant         Event Service   
227         Boat or Ferry              Bus Stop         Women's Store   
245                  Park            Theme Park        Discount Store   
254        Cosmetics Shop                  Park           Coffee Shop   
256         Deli / Bodega              Bus Stop   Filipino Restaurant   
285           Pizza Place           Video Store  Ethiopian Restaurant   
303         Women's Store  Ethiopian Restaurant         Event Service   
305          Cocktail Bar              Bus Stop        Sandwich Place   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
27          Boat or Ferry              Bus Stop         Event Service   
193           Event Space               Exhibit            Eye Doctor   
198      Botanical Garden            Playground        Discount Store   
202           Event Space               Exhibit            Eye Doctor   
204         Women's Store                 Field           Event Space   
224         Women's Store  Fast Food Restaurant         Event Service   
226           Event Space               Exhibit            Eye Doctor   
227   Filipino Restaurant           Event Space               Exhibit   
245                  Food                  Farm  Ethiopian Restaurant   
254         Deli / Bodega              Bus Stop    Athletics & Sports   
256         Event Service           Event Space               Exhibit   
285         Event Service           Event Space               Exhibit   
303           Event Space               Exhibit            Eye Doctor   
305         Women's Store        Farmers Market  Ethiopian Restaurant   

    9th Most Common Venue 10th Most Common Venue  
27            Event Space                Exhibit  
193               Factory     Falafel Restaurant  
198                  Farm   Fast Food Restaurant  
202               Factory     Falafel Restaurant  
204               Exhibit             Eye Doctor  
224           Event Space                Exhibit  
226               Factory     Falafel Restaurant  
227            Eye Doctor                Factory  
245            Food Stand             Food Court  
254           Supermarket          Tattoo Parlor  
256            Eye Doctor                Factory  
285            Eye Doctor                Factory  
303               Factory     Falafel Restaurant  
305         Event Service         

In [42]:
newyork_merged.loc[newyork_merged['Cluster Labels'] == 3, newyork_merged.columns[[1] + list(range(5, newyork_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
207   Port Ivory                   Bar         Women's Store   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
207                 Field  Ethiopian Restaurant         Event Service   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
207           Event Space               Exhibit            Eye Doctor   

    9th Most Common Venue 10th Most Common Venue  
207               Factory     Falafel Restaurant

In [43]:
newyork_merged.loc[newyork_merged['Cluster Labels'] == 4, newyork_merged.columns[[1] + list(range(5, newyork_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
76  Mill Island                  Pool         Women's Store   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
76   Filipino Restaurant  Ethiopian Restaurant         Event Service   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
76           Event Space               Exhibit            Eye Doctor   

   9th Most Common Venue 10th Most Common Venue  
76               Factory     Falafel Restaurant

In [44]:
source = requests.get('https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M').text

In [45]:
soup = BeautifulSoup(source, 'lxml')
print(soup.prettify())

<!DOCTYPE html>
<html class="client-nojs" dir="ltr" lang="en">
 <head>
  <meta charset="utf-8"/>
  <title>
   List of postal codes of Canada: M - Wikipedia
  </title>
  <script>
   document.documentElement.className="client-js";RLCONF={"wgBreakFrames":!1,"wgSeparatorTransformTable":["",""],"wgDigitTransformTable":["",""],"wgDefaultDateFormat":"dmy","wgMonthNames":["","January","February","March","April","May","June","July","August","September","October","November","December"],"wgMonthNamesShort":["","Jan","Feb","Mar","Apr","May","Jun","Jul","Aug","Sep","Oct","Nov","Dec"],"wgRequestId":"XcWTHgpAADkAAIKIYKoAAABS","wgCSPNonce":!1,"wgCanonicalNamespace":"","wgCanonicalSpecialPageName":!1,"wgNamespaceNumber":0,"wgPageName":"List_of_postal_codes_of_Canada:_M","wgTitle":"List of postal codes of Canada: M","wgCurRevisionId":920980179,"wgRevisionId":920980179,"wgArticleId":539066,"wgIsArticle":!0,"wgIsRedirect":!1,"wgAction":"view","wgUserName":null,"wgUserGroups":["*"],"wgCategories":["Communi

In [46]:
table = soup.find('table')

In [47]:
tablerows = table.findAll('tr')
res = []

In [48]:
for tr in tablerows:
    row = tr.find_all('td')
    row = [tr.text.strip() for tr in row]
    if row:
        res.append(row)
df = pd.DataFrame(res, columns=["PostalCode", "Borough", "Neighborhood"])

In [49]:
df

PostalCode           Borough  \
0          M1A      Not assigned   
1          M2A      Not assigned   
2          M3A        North York   
3          M4A        North York   
4          M5A  Downtown Toronto   
5          M5A  Downtown Toronto   
6          M6A        North York   
7          M6A        North York   
8          M7A      Queen's Park   
9          M8A      Not assigned   
10         M9A         Etobicoke   
11         M1B       Scarborough   
12         M1B       Scarborough   
13         M2B      Not assigned   
14         M3B        North York   
15         M4B         East York   
16         M4B         East York   
17         M5B  Downtown Toronto   
18         M5B  Downtown Toronto   
19         M6B        North York   
20         M7B      Not assigned   
21         M8B      Not assigned   
22         M9B         Etobicoke   
23         M9B         Etobicoke   
24         M9B         Etobicoke   
25         M9B         Etobicoke   
26         M9B         Etobicoke   
27         M1C       Scarborough   
28         M1C       Scarborough   
29         M1C       Scarborough   
30         M2C      Not assigned   
31         M3C        North York   
32         M3C        North York   
33         M4C         East York   
34         M5C  Downtown Toronto   
35         M6C              York   
36         M7C      Not assigned   
37         M8C      Not assigned   
38         M9C         Etobicoke   
39         M9C         Etobicoke   
40         M9C         Etobicoke   
41         M9C         Etobicoke   
42         M1E       Scarborough   
43         M1E       Scarborough   
44         M1E       Scarborough   
45         M2E      Not assigned   
46         M3E      Not assigned   
47         M4E      East Toronto   
48         M5E  Downtown Toronto   
49         M6E              York   
50         M7E      Not assigned   
51         M8E      Not assigned   
52         M9E      Not assigned   
53         M1G       Scarborough   
54         M2G      Not assigned   
55         M3G      Not assigned   
56         M4G         East York   
57         M5G  Downtown Toronto   
58         M6G  Downtown Toronto   
59         M7G      Not assigned   
60         M8G      Not assigned   
61         M9G      Not assigned   
62         M1H       Scarborough   
63         M2H        North York   
64         M3H        North York   
65         M3H        North York   
66         M3H        North York   
67         M4H         East York   
68         M5H  Downtown Toronto   
69         M5H  Downtown Toronto   
70         M5H  Downtown Toronto   
71         M6H      West Toronto   
72         M6H      West Toronto   
73         M7H      Not assigned   
74         M8H      Not assigned   
75         M9H      Not assigned   
76         M1J       Scarborough   
77         M2J        North York   
78         M2J        North York   
79         M2J        North York   
80         M3J        North York   
81         M3J        North York   
82         M4J         East York   
83         M5J  Downtown Toronto   
84         M5J  Downtown Toronto   
85         M5J  Downtown Toronto   
86         M6J      West Toronto   
87         M6J      West Toronto   
88         M7J      Not assigned   
89         M8J      Not assigned   
90         M9J      Not assigned   
91         M1K       Scarborough   
92         M1K       Scarborough   
93         M1K       Scarborough   
94         M2K        North York   
95         M3K        North York   
96         M3K        North York   
97         M4K      East Toronto   
98         M4K      East Toronto   
99         M5K  Downtown Toronto   
100        M5K  Downtown Toronto   
101        M6K      West Toronto   
102        M6K      West Toronto   
103        M6K      West Toronto   
104        M7K      Not assigned   
105        M8K      Not assigned   
106        M9K      Not assigned   
107        M1L       Scarborough   
108        M1L       Scarborough   
109        M1L       Scarborough   
110     

In [50]:
df['Borough'] = df['Borough'].replace('Not assigned', np.nan)
df = df.dropna(axis=0, subset=['Borough'])

In [51]:
df.loc[df['Neighborhood'] == 'Not assigned', 'Neighborhood'] = "Queen's Park"

/opt/conda/envs/Python36/lib/python3.6/site-packages/pandas/core/indexing.py:190: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self._setitem_with_indexer(indexer, value)
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  if __name__ == '__main__':


In [52]:
df

PostalCode           Borough  \
2          M3A        North York   
3          M4A        North York   
4          M5A  Downtown Toronto   
5          M5A  Downtown Toronto   
6          M6A        North York   
7          M6A        North York   
8          M7A      Queen's Park   
10         M9A         Etobicoke   
11         M1B       Scarborough   
12         M1B       Scarborough   
14         M3B        North York   
15         M4B         East York   
16         M4B         East York   
17         M5B  Downtown Toronto   
18         M5B  Downtown Toronto   
19         M6B        North York   
22         M9B         Etobicoke   
23         M9B         Etobicoke   
24         M9B         Etobicoke   
25         M9B         Etobicoke   
26         M9B         Etobicoke   
27         M1C       Scarborough   
28         M1C       Scarborough   
29         M1C       Scarborough   
31         M3C        North York   
32         M3C        North York   
33         M4C         East York   
34         M5C  Downtown Toronto   
35         M6C              York   
38         M9C         Etobicoke   
39         M9C         Etobicoke   
40         M9C         Etobicoke   
41         M9C         Etobicoke   
42         M1E       Scarborough   
43         M1E       Scarborough   
44         M1E       Scarborough   
47         M4E      East Toronto   
48         M5E  Downtown Toronto   
49         M6E              York   
53         M1G       Scarborough   
56         M4G         East York   
57         M5G  Downtown Toronto   
58         M6G  Downtown Toronto   
62         M1H       Scarborough   
63         M2H        North York   
64         M3H        North York   
65         M3H        North York   
66         M3H        North York   
67         M4H         East York   
68         M5H  Downtown Toronto   
69         M5H  Downtown Toronto   
70         M5H  Downtown Toronto   
71         M6H      West Toronto   
72         M6H      West Toronto   
76         M1J       Scarborough   
77         M2J        North York   
78         M2J        North York   
79         M2J        North York   
80         M3J        North York   
81         M3J        North York   
82         M4J         East York   
83         M5J  Downtown Toronto   
84         M5J  Downtown Toronto   
85         M5J  Downtown Toronto   
86         M6J      West Toronto   
87         M6J      West Toronto   
91         M1K       Scarborough   
92         M1K       Scarborough   
93         M1K       Scarborough   
94         M2K        North York   
95         M3K        North York   
96         M3K        North York   
97         M4K      East Toronto   
98         M4K      East Toronto   
99         M5K  Downtown Toronto   
100        M5K  Downtown Toronto   
101        M6K      West Toronto   
102        M6K      West Toronto   
103        M6K      West Toronto   
107        M1L       Scarborough   
108        M1L       Scarborough   
109        M1L       Scarborough   
110        M2L        North York   
111        M2L        North York   
112        M3L        North York   
113        M4L      East Toronto   
114        M4L      East Toronto   
115        M5L  Downtown Toronto   
116        M5L  Downtown Toronto   
117        M6L        North York   
118        M6L        North York   
119        M6L        North York   
122        M9L        North York   
123        M1M       Scarborough   
124        M1M       Scarborough   
125        M1M       Scarborough   
126        M2M        North York   
127        M2M        North York   
128        M3M        North York   
129        M4M      East Toronto   
130        M5M        North York   
131        M5M        North York   
132        M6M              York   
133        M6M              York   
134        M6M              York   
135        M6M              York   
138        M9M        North York   
139        M9M        North York   
140        M1N       Scarborough   
141        M1N       Scarborough   
142     

In [53]:
df1 = df.groupby(['PostalCode','Borough'],as_index=False, sort=False).agg(','.join)
df1

PostalCode           Borough  \
0          M3A        North York   
1          M4A        North York   
2          M5A  Downtown Toronto   
3          M6A        North York   
4          M7A      Queen's Park   
5          M9A         Etobicoke   
6          M1B       Scarborough   
7          M3B        North York   
8          M4B         East York   
9          M5B  Downtown Toronto   
10         M6B        North York   
11         M9B         Etobicoke   
12         M1C       Scarborough   
13         M3C        North York   
14         M4C         East York   
15         M5C  Downtown Toronto   
16         M6C              York   
17         M9C         Etobicoke   
18         M1E       Scarborough   
19         M4E      East Toronto   
20         M5E  Downtown Toronto   
21         M6E              York   
22         M1G       Scarborough   
23         M4G         East York   
24         M5G  Downtown Toronto   
25         M6G  Downtown Toronto   
26         M1H       Scarborough   
27         M2H        North York   
28         M3H        North York   
29         M4H         East York   
30         M5H  Downtown Toronto   
31         M6H      West Toronto   
32         M1J       Scarborough   
33         M2J        North York   
34         M3J        North York   
35         M4J         East York   
36         M5J  Downtown Toronto   
37         M6J      West Toronto   
38         M1K       Scarborough   
39         M2K        North York   
40         M3K        North York   
41         M4K      East Toronto   
42         M5K  Downtown Toronto   
43         M6K      West Toronto   
44         M1L       Scarborough   
45         M2L        North York   
46         M3L        North York   
47         M4L      East Toronto   
48         M5L  Downtown Toronto   
49         M6L        North York   
50         M9L        North York   
51         M1M       Scarborough   
52         M2M        North York   
53         M3M        North York   
54         M4M      East Toronto   
55         M5M        North York   
56         M6M              York   
57         M9M        North York   
58         M1N       Scarborough   
59         M2N        North York   
60         M3N        North York   
61         M4N   Central Toronto   
62         M5N   Central Toronto   
63         M6N              York   
64         M9N              York   
65         M1P       Scarborough   
66         M2P        North York   
67         M4P   Central Toronto   
68         M5P   Central Toronto   
69         M6P      West Toronto   
70         M9P         Etobicoke   
71         M1R       Scarborough   
72         M2R        North York   
73         M4R   Central Toronto   
74         M5R   Central Toronto   
75         M6R      West Toronto   
76         M7R       Mississauga   
77         M9R         Etobicoke   
78         M1S       Scarborough   
79         M4S   Central Toronto   
80         M5S  Downtown Toronto   
81         M6S      West Toronto   
82         M1T       Scarborough   
83         M4T   Central Toronto   
84         M5T  Downtown Toronto   
85         M1V       Scarborough   
86         M4V   Central Toronto   
87         M5V  Downtown Toronto   
88         M8V         Etobicoke   
89         M9V         Etobicoke   
90         M1W       Scarborough   
91         M4W  Downtown Toronto   
92         M5W  Downtown Toronto   
93         M8W         Etobicoke   
94         M9W         Etobicoke   
95         M1X       Scarborough   
96         M4X  Downtown Toronto   
97         M5X  Downtown Toronto   
98         M8X         Etobicoke   
99         M4Y  Downtown Toronto   
100        M7Y      East Toronto   
101        M8Y         Etobicoke   
102        M8Z         Etobicoke   

                                          Neighborhood  
0                                            Parkwoods  
1                                     Victoria Village  
2                             Harbourfront,Regent Park  
3                      Lawrence

In [54]:
df1.shape

(103, 3)

In [55]:
file_name = 'https://cocl.us/Geospatial_data'
df2 = pd.read_csv(file_name)

In [56]:
df2

Postal Code   Latitude  Longitude
0           M1B  43.806686 -79.194353
1           M1C  43.784535 -79.160497
2           M1E  43.763573 -79.188711
3           M1G  43.770992 -79.216917
4           M1H  43.773136 -79.239476
5           M1J  43.744734 -79.239476
6           M1K  43.727929 -79.262029
7           M1L  43.711112 -79.284577
8           M1M  43.716316 -79.239476
9           M1N  43.692657 -79.264848
10          M1P  43.757410 -79.273304
11          M1R  43.750072 -79.295849
12          M1S  43.794200 -79.262029
13          M1T  43.781638 -79.304302
14          M1V  43.815252 -79.284577
15          M1W  43.799525 -79.318389
16          M1X  43.836125 -79.205636
17          M2H  43.803762 -79.363452
18          M2J  43.778517 -79.346556
19          M2K  43.786947 -79.385975
20          M2L  43.757490 -79.374714
21          M2M  43.789053 -79.408493
22          M2N  43.770120 -79.408493
23          M2P  43.752758 -79.400049
24          M2R  43.782736 -79.442259
25          M3A  43.753259 -79.329656
26          M3B  43.745906 -79.352188
27          M3C  43.725900 -79.340923
28          M3H  43.754328 -79.442259
29          M3J  43.767980 -79.487262
30          M3K  43.737473 -79.464763
31          M3L  43.739015 -79.506944
32          M3M  43.728496 -79.495697
33          M3N  43.761631 -79.520999
34          M4A  43.725882 -79.315572
35          M4B  43.706397 -79.309937
36          M4C  43.695344 -79.318389
37          M4E  43.676357 -79.293031
38          M4G  43.709060 -79.363452
39          M4H  43.705369 -79.349372
40          M4J  43.685347 -79.338106
41          M4K  43.679557 -79.352188
42          M4L  43.668999 -79.315572
43          M4M  43.659526 -79.340923
44          M4N  43.728020 -79.388790
45          M4P  43.712751 -79.390197
46          M4R  43.715383 -79.405678
47          M4S  43.704324 -79.388790
48          M4T  43.689574 -79.383160
49          M4V  43.686412 -79.400049
50          M4W  43.679563 -79.377529
51          M4X  43.667967 -79.367675
52          M4Y  43.665860 -79.383160
53          M5A  43.654260 -79.360636
54          M5B  43.657162 -79.378937
55          M5C  43.651494 -79.375418
56          M5E  43.644771 -79.373306
57          M5G  43.657952 -79.387383
58          M5H  43.650571 -79.384568
59          M5J  43.640816 -79.381752
60          M5K  43.647177 -79.381576
61          M5L  43.648198 -79.379817
62          M5M  43.733283 -79.419750
63          M5N  43.711695 -79.416936
64          M5P  43.696948 -79.411307
65          M5R  43.672710 -79.405678
66          M5S  43.662696 -79.400049
67          M5T  43.653206 -79.400049
68          M5V  43.628947 -79.394420
69          M5W  43.646435 -79.374846
70          M5X  43.648429 -79.382280
71          M6A  43.718518 -79.464763
72          M6B  43.709577 -79.445073
73          M6C  43.693781 -79.428191
74          M6E  43.689026 -79.453512
75          M6G  43.669542 -79.422564
76          M6H  43.669005 -79.442259
77          M6J  43.647927 -79.419750
78          M6K  43.636847 -79.428191
79          M6L  43.713756 -79.490074
80          M6M  43.691116 -79.476013
81          M6N  43.673185 -79.487262
82          M6P  43.661608 -79.464763
83          M6R  43.648960 -79.456325
84          M6S  43.651571 -79.484450
85          M7A  43.662301 -79.389494
86          M7R  43.636966 -79.615819
87          M7Y  43.662744 -79.321558
88          M8V  43.605647 -79.501321
89          M8W  43.602414 -79.543484
90          M8X  43.653654 -79.506944
91          M8Y  43.636258 -79.498509
92          M8Z  43.628841 -79.520999
93          M9A  43.667856 -79.532242
94          M9B  43.650943 -79.554724
95          M9C  43.643515 -79.577201
96          M9L  43.756303 -79.565963
97          M9M  43.724766 -79.532242
98          M9N  43.706876 -79.518188
99          M9P  43.696319 -79.532242
100         M9R  43.688905 -79.554724
101         M9V  43.739416 -79.588437
102         M9W  43.706748 -79.594054

In [57]:
df2= df2.rename(columns={"Postal Code":"PostalCode"})

In [58]:
df2

PostalCode   Latitude  Longitude
0          M1B  43.806686 -79.194353
1          M1C  43.784535 -79.160497
2          M1E  43.763573 -79.188711
3          M1G  43.770992 -79.216917
4          M1H  43.773136 -79.239476
5          M1J  43.744734 -79.239476
6          M1K  43.727929 -79.262029
7          M1L  43.711112 -79.284577
8          M1M  43.716316 -79.239476
9          M1N  43.692657 -79.264848
10         M1P  43.757410 -79.273304
11         M1R  43.750072 -79.295849
12         M1S  43.794200 -79.262029
13         M1T  43.781638 -79.304302
14         M1V  43.815252 -79.284577
15         M1W  43.799525 -79.318389
16         M1X  43.836125 -79.205636
17         M2H  43.803762 -79.363452
18         M2J  43.778517 -79.346556
19         M2K  43.786947 -79.385975
20         M2L  43.757490 -79.374714
21         M2M  43.789053 -79.408493
22         M2N  43.770120 -79.408493
23         M2P  43.752758 -79.400049
24         M2R  43.782736 -79.442259
25         M3A  43.753259 -79.329656
26         M3B  43.745906 -79.352188
27         M3C  43.725900 -79.340923
28         M3H  43.754328 -79.442259
29         M3J  43.767980 -79.487262
30         M3K  43.737473 -79.464763
31         M3L  43.739015 -79.506944
32         M3M  43.728496 -79.495697
33         M3N  43.761631 -79.520999
34         M4A  43.725882 -79.315572
35         M4B  43.706397 -79.309937
36         M4C  43.695344 -79.318389
37         M4E  43.676357 -79.293031
38         M4G  43.709060 -79.363452
39         M4H  43.705369 -79.349372
40         M4J  43.685347 -79.338106
41         M4K  43.679557 -79.352188
42         M4L  43.668999 -79.315572
43         M4M  43.659526 -79.340923
44         M4N  43.728020 -79.388790
45         M4P  43.712751 -79.390197
46         M4R  43.715383 -79.405678
47         M4S  43.704324 -79.388790
48         M4T  43.689574 -79.383160
49         M4V  43.686412 -79.400049
50         M4W  43.679563 -79.377529
51         M4X  43.667967 -79.367675
52         M4Y  43.665860 -79.383160
53         M5A  43.654260 -79.360636
54         M5B  43.657162 -79.378937
55         M5C  43.651494 -79.375418
56         M5E  43.644771 -79.373306
57         M5G  43.657952 -79.387383
58         M5H  43.650571 -79.384568
59         M5J  43.640816 -79.381752
60         M5K  43.647177 -79.381576
61         M5L  43.648198 -79.379817
62         M5M  43.733283 -79.419750
63         M5N  43.711695 -79.416936
64         M5P  43.696948 -79.411307
65         M5R  43.672710 -79.405678
66         M5S  43.662696 -79.400049
67         M5T  43.653206 -79.400049
68         M5V  43.628947 -79.394420
69         M5W  43.646435 -79.374846
70         M5X  43.648429 -79.382280
71         M6A  43.718518 -79.464763
72         M6B  43.709577 -79.445073
73         M6C  43.693781 -79.428191
74         M6E  43.689026 -79.453512
75         M6G  43.669542 -79.422564
76         M6H  43.669005 -79.442259
77         M6J  43.647927 -79.419750
78         M6K  43.636847 -79.428191
79         M6L  43.713756 -79.490074
80         M6M  43.691116 -79.476013
81         M6N  43.673185 -79.487262
82         M6P  43.661608 -79.464763
83         M6R  43.648960 -79.456325
84         M6S  43.651571 -79.484450
85         M7A  43.662301 -79.389494
86         M7R  43.636966 -79.615819
87         M7Y  43.662744 -79.321558
88         M8V  43.605647 -79.501321
89         M8W  43.602414 -79.543484
90         M8X  43.653654 -79.506944
91         M8Y  43.636258 -79.498509
92         M8Z  43.628841 -79.520999
93         M9A  43.667856 -79.532242
94         M9B  43.650943 -79.554724
95         M9C  43.643515 -79.577201
96         M9L  43.756303 -79.565963
97         M9M  43.724766 -79.532242
98         M9N  43.706876 -79.518188
99         M9P  43.696319 -79.532242
100        M9R  43.688905 -79.554724
101        M9V  43.739416 -79.588437
102        M9W  43.706748 -79.594054

In [59]:
df3 = pd.merge(left=df1,right=df2, left_on='PostalCode', right_on='PostalCode')
df3

PostalCode           Borough  \
0          M3A        North York   
1          M4A        North York   
2          M5A  Downtown Toronto   
3          M6A        North York   
4          M7A      Queen's Park   
5          M9A         Etobicoke   
6          M1B       Scarborough   
7          M3B        North York   
8          M4B         East York   
9          M5B  Downtown Toronto   
10         M6B        North York   
11         M9B         Etobicoke   
12         M1C       Scarborough   
13         M3C        North York   
14         M4C         East York   
15         M5C  Downtown Toronto   
16         M6C              York   
17         M9C         Etobicoke   
18         M1E       Scarborough   
19         M4E      East Toronto   
20         M5E  Downtown Toronto   
21         M6E              York   
22         M1G       Scarborough   
23         M4G         East York   
24         M5G  Downtown Toronto   
25         M6G  Downtown Toronto   
26         M1H       Scarborough   
27         M2H        North York   
28         M3H        North York   
29         M4H         East York   
30         M5H  Downtown Toronto   
31         M6H      West Toronto   
32         M1J       Scarborough   
33         M2J        North York   
34         M3J        North York   
35         M4J         East York   
36         M5J  Downtown Toronto   
37         M6J      West Toronto   
38         M1K       Scarborough   
39         M2K        North York   
40         M3K        North York   
41         M4K      East Toronto   
42         M5K  Downtown Toronto   
43         M6K      West Toronto   
44         M1L       Scarborough   
45         M2L        North York   
46         M3L        North York   
47         M4L      East Toronto   
48         M5L  Downtown Toronto   
49         M6L        North York   
50         M9L        North York   
51         M1M       Scarborough   
52         M2M        North York   
53         M3M        North York   
54         M4M      East Toronto   
55         M5M        North York   
56         M6M              York   
57         M9M        North York   
58         M1N       Scarborough   
59         M2N        North York   
60         M3N        North York   
61         M4N   Central Toronto   
62         M5N   Central Toronto   
63         M6N              York   
64         M9N              York   
65         M1P       Scarborough   
66         M2P        North York   
67         M4P   Central Toronto   
68         M5P   Central Toronto   
69         M6P      West Toronto   
70         M9P         Etobicoke   
71         M1R       Scarborough   
72         M2R        North York   
73         M4R   Central Toronto   
74         M5R   Central Toronto   
75         M6R      West Toronto   
76         M7R       Mississauga   
77         M9R         Etobicoke   
78         M1S       Scarborough   
79         M4S   Central Toronto   
80         M5S  Downtown Toronto   
81         M6S      West Toronto   
82         M1T       Scarborough   
83         M4T   Central Toronto   
84         M5T  Downtown Toronto   
85         M1V       Scarborough   
86         M4V   Central Toronto   
87         M5V  Downtown Toronto   
88         M8V         Etobicoke   
89         M9V         Etobicoke   
90         M1W       Scarborough   
91         M4W  Downtown Toronto   
92         M5W  Downtown Toronto   
93         M8W         Etobicoke   
94         M9W         Etobicoke   
95         M1X       Scarborough   
96         M4X  Downtown Toronto   
97         M5X  Downtown Toronto   
98         M8X         Etobicoke   
99         M4Y  Downtown Toronto   
100        M7Y      East Toronto   
101        M8Y         Etobicoke   
102        M8Z         Etobicoke   

                                          Neighborhood   Latitude  Longitude  
0                                            Parkwoods  43.753259 -79.329656  
1                                     Victoria Village  43.725882 -79.315572  
2                     

In [60]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(df3['Borough'].unique()),
        df3.shape[0]
    )
)

The dataframe has 11 boroughs and 103 neighborhoods.


In [61]:
address = 'Toronto, Canada'

geolocator = Nominatim(user_agent="toronto_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Toronto are 43.653963, -79.387207.


In [62]:
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=10)

for lat, lng, borough, neighborhood in zip(df3['Latitude'], df3['Longitude'], df3['Borough'], df3['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto)  
    
map_toronto

In [63]:
toronto_data = df3
toronto_data.head()

PostalCode           Borough                     Neighborhood   Latitude  \
0        M3A        North York                        Parkwoods  43.753259   
1        M4A        North York                 Victoria Village  43.725882   
2        M5A  Downtown Toronto         Harbourfront,Regent Park  43.654260   
3        M6A        North York  Lawrence Heights,Lawrence Manor  43.718518   
4        M7A      Queen's Park                     Queen's Park  43.662301   

   Longitude  
0 -79.329656  
1 -79.315572  
2 -79.360636  
3 -79.464763  
4 -79.389494

In [64]:
CLIENT_ID = 'E5KVN2UWQURTJMYS3ZFOJDUYA3IV3PGB3ELPVRGRIV4UDODD'
CLIENT_SECRET = 'CYN0UAZQU2XCNFCG0QJUOXBM5HXVDN0F2YP0EQXKU4KINESA'
VERSION = '20180605'

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: E5KVN2UWQURTJMYS3ZFOJDUYA3IV3PGB3ELPVRGRIV4UDODD
CLIENT_SECRET:CYN0UAZQU2XCNFCG0QJUOXBM5HXVDN0F2YP0EQXKU4KINESA


In [65]:
toronto_data.loc[0, 'Neighborhood']

'Parkwoods'

In [66]:
neighborhood_latitude = toronto_data.loc[0, 'Latitude']
neighborhood_longitude = toronto_data.loc[0, 'Longitude']

neighborhood_name = toronto_data.loc[0, 'Neighborhood']

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))

Latitude and longitude values of Parkwoods are 43.7532586, -79.3296565.


In [67]:
LIMIT = 100
radius = 500
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)
url

'https://api.foursquare.com/v2/venues/explore?&client_id=E5KVN2UWQURTJMYS3ZFOJDUYA3IV3PGB3ELPVRGRIV4UDODD&client_secret=CYN0UAZQU2XCNFCG0QJUOXBM5HXVDN0F2YP0EQXKU4KINESA&v=20180605&ll=43.7532586,-79.3296565&radius=500&limit=100'

In [68]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5dc59e01be7078002c31113b'},
 'response': {'warning': {'text': "There aren't a lot of results near you. Try something more general, reset your filters, or expand the search area."},
  'headerLocation': 'Parkwoods - Donalda',
  'headerFullLocation': 'Parkwoods - Donalda, Toronto',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 2,
  'suggestedBounds': {'ne': {'lat': 43.757758604500005,
    'lng': -79.32343823984928},
   'sw': {'lat': 43.7487585955, 'lng': -79.33587476015072}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4e8d9dcdd5fbbbb6b3003c7b',
       'name': 'Brookbanks Park',
       'location': {'address': 'Toronto',
        'lat': 43.751976046055574,
        'lng': -79.33214044722958,
        'labeledLatLngs': 

In [69]:
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [70]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues)

filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

name         categories        lat        lng
0  Brookbanks Park               Park  43.751976 -79.332140
1    Variety Store  Food & Drink Shop  43.751974 -79.333114

In [71]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

2 venues were returned by Foursquare.


In [72]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [76]:
toronto_venues = getNearbyVenues(names=toronto_data['Neighborhood'],
                                   latitudes=toronto_data['Latitude'],
                                   longitudes=toronto_data['Longitude']
                                  )

Parkwoods
Victoria Village
Harbourfront,Regent Park
Lawrence Heights,Lawrence Manor
Queen's Park
Islington Avenue
Rouge,Malvern
Don Mills North
Woodbine Gardens,Parkview Hill
Ryerson,Garden District
Glencairn
Cloverdale,Islington,Martin Grove,Princess Gardens,West Deane Park
Highland Creek,Rouge Hill,Port Union
Flemingdon Park,Don Mills South
Woodbine Heights
St. James Town
Humewood-Cedarvale
Bloordale Gardens,Eringate,Markland Wood,Old Burnhamthorpe
Guildwood,Morningside,West Hill
The Beaches
Berczy Park
Caledonia-Fairbanks
Woburn
Leaside
Central Bay Street
Christie
Cedarbrae
Hillcrest Village
Bathurst Manor,Downsview North,Wilson Heights
Thorncliffe Park
Adelaide,King,Richmond
Dovercourt Village,Dufferin
Scarborough Village
Fairview,Henry Farm,Oriole
Northwood Park,York University
East Toronto
Harbourfront East,Toronto Islands,Union Station
Little Portugal,Trinity
East Birchmount Park,Ionview,Kennedy Park
Bayview Village
CFB Toronto,Downsview East
The Danforth West,Riverdale
Design E

In [77]:
print(toronto_venues.shape)
toronto_venues.head()

(2233, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0         Parkwoods              43.753259              -79.329656   
1         Parkwoods              43.753259              -79.329656   
2  Victoria Village              43.725882              -79.315572   
3  Victoria Village              43.725882              -79.315572   
4  Victoria Village              43.725882              -79.315572   

                    Venue  Venue Latitude  Venue Longitude  \
0         Brookbanks Park       43.751976       -79.332140   
1           Variety Store       43.751974       -79.333114   
2  Victoria Village Arena       43.723481       -79.315635   
3             Tim Hortons       43.725517       -79.313103   
4               Portugril       43.725819       -79.312785   

          Venue Category  
0                   Park  
1      Food & Drink Shop  
2           Hockey Arena  
3            Coffee Shop  
4  Portuguese Restaurant

In [78]:
toronto_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                                
Adelaide,King,Richmond                                                100   
Agincourt                                                               4   
Agincourt North,L'Amoreaux East,Milliken,Steele...                      2   
Albion Gardens,Beaumond Heights,Humbergate,Jame...                      7   
Alderwood,Long Branch                                                   9   
Bathurst Manor,Downsview North,Wilson Heights                          19   
Bayview Village                                                         4   
Bedford Park,Lawrence Manor East                                       24   
Berczy Park                                                            55   
Birch Cliff,Cliffside West                                              4   
Bloordale Gardens,Eringate,Markland Wood,Old Bu...                      9   
Brockton,Exhibition Place,Parkdale Village                             22   
Business Reply Mail Processing Centre 969 Eastern                      15   
CFB Toronto,Downsview East                                              3   
CN Tower,Bathurst Quay,Island airport,Harbourfr...                     15   
Cabbagetown,St. James Town                                             45   
Caledonia-Fairbanks                                                     5   
Canada Post Gateway Processing Centre                                  11   
Cedarbrae                                                               7   
Central Bay Street                                                     79   
Chinatown,Grange Park,Kensington Market                                93   
Christie                                                               17   
Church and Wellesley                                                   86   
Clairlea,Golden Mile,Oakridge                                          10   
Clarks Corners,Sullivan,Tam O'Shanter                                   9   
Cliffcrest,Cliffside,Scarborough Village West                           2   
Cloverdale,Islington,Martin Grove,Princess Gard...                      2   
Commerce Court,Victoria Hotel                                         100   
Davisville                                                             32   
Davisville North                                                        8   
Deer Park,Forest Hill SE,Rathnelly,South Hill,S...                     15   
Del Ray,Keelesdale,Mount Dennis,Silverthorn                             4   
Design Exchange,Toronto Dominion Centre                               100   
Don Mills North                                                         5   
Dorset Park,Scarborough Town Centre,Wexford Hei...                      6   
Dovercourt Village,Dufferin                                            17   
Downsview Central                                                       3   
Downsview Northwest                                                     5   
Downsview West                                                          4   
Downsview,North Park,Upwood Park                                        5   
East Birchmount Park,Ionview,Kennedy Park                               4   
East Toronto                                                            3   
Emery,Humberlea                                                         2   
Fairview,Henry Farm,Oriole                                             66   
First Canadian Place,Underground city                                 100   
Flemingdon Park,Don Mills South                                        21   
Forest Hill North,Forest Hill West                                      4   
Glencairn                                                               4   
Guildwood,Morningside,West Hill                                         7   
Harbord,University of Toronto                                          36   
Harbourfront East,Toronto Islands,Union Station 

In [79]:
print('There are {} uniques categories.'.format(len(toronto_venues['Venue Category'].unique())))

There are 274 uniques categories.


In [80]:
toronto_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")

toronto_onehot['Neighborhood'] = toronto_venues['Neighborhood'] 

fixed_columns = [toronto_onehot.columns[-1]] + list(toronto_onehot.columns[:-1])
toronto_onehot = toronto_onehot[fixed_columns]

toronto_onehot.head()

Yoga Studio  Accessories Store  Afghan Restaurant  Airport  \
0            0                  0                  0        0   
1            0                  0                  0        0   
2            0                  0                  0        0   
3            0                  0                  0        0   
4            0                  0                  0        0   

   Airport Food Court  Airport Gate  Airport Lounge  Airport Service  \
0                   0             0               0                0   
1                   0             0               0                0   
2                   0             0               0                0   
3                   0             0               0                0   
4                   0             0               0                0   

   Airport Terminal  American Restaurant  Antique Shop  Aquarium  Art Gallery  \
0                 0                    0             0         0            0   
1                 0                    0             0         0            0   
2                 0                    0             0         0            0   
3                 0                    0             0         0            0   
4                 0                    0             0         0            0   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  Auto Garage  \
0                    0                 0                   0            0   
1                    0                 0                   0            0   
2                    0                 0                   0            0   
3                    0                 0                   0            0   
4                    0                 0                   0            0   

   Auto Workshop  BBQ Joint  Baby Store  Bagel Shop  Bakery  Bank  Bar  \
0              0          0           0           0       0     0    0   
1              0          0           0           0       0     0    0   
2              0          0           0           0       0     0    0   
3              0          0           0           0       0     0    0   
4              0          0           0           0       0     0    0   

   Baseball Field  Baseball Stadium  Basketball Court  Basketball Stadium  \
0               0                 0                 0                   0   
1               0                 0                 0                   0   
2               0                 0                 0                   0   
3               0                 0                 0                   0   
4               0                 0                 0                   0   

   Beach  Bed & Breakfast  Beer Bar  Beer Store  Belgian Restaurant  \
0      0                0         0           0                   0   
1      0                0         0           0                   0   
2      0                0         0           0                   0   
3      0                0         0           0                   0   
4      0                0         0           0                   0   

   Bike Shop  Bistro  Boat or Ferry  Bookstore  Boutique  \
0          0       0              0          0         0   
1          0       0              0          0         0   
2          0       0              0          0         0   
3          0       0              0          0         0   
4          0       0              0          0         0   

   Brazilian Restaurant  Breakfast Spot  Brewery  Bridal Shop  \
0                     0               0        0            0   
1                     0               0        0            0   
2                     0               0        0            0   
3                     0               0        0            0   
4                     0               0        0            0   

   Bubble Tea Shop  Building  Burger Joint  Burrito Place  Bus Line  \
0                0         0             0              0         0   


In [81]:
toronto_onehot.shape

(2233, 274)

In [82]:
toronto_grouped = toronto_onehot.groupby('Neighborhood').mean().reset_index()
toronto_grouped

Neighborhood  Yoga Studio  \
0                               Adelaide,King,Richmond     0.000000   
1                                            Agincourt     0.000000   
2    Agincourt North,L'Amoreaux East,Milliken,Steel...     0.000000   
3    Albion Gardens,Beaumond Heights,Humbergate,Jam...     0.000000   
4                                Alderwood,Long Branch     0.000000   
5        Bathurst Manor,Downsview North,Wilson Heights     0.000000   
6                                      Bayview Village     0.000000   
7                     Bedford Park,Lawrence Manor East     0.000000   
8                                          Berczy Park     0.000000   
9                           Birch Cliff,Cliffside West     0.000000   
10   Bloordale Gardens,Eringate,Markland Wood,Old B...     0.000000   
11          Brockton,Exhibition Place,Parkdale Village     0.000000   
12   Business Reply Mail Processing Centre 969 Eastern     0.000000   
13                          CFB Toronto,Downsview East     0.000000   
14   CN Tower,Bathurst Quay,Island airport,Harbourf...     0.000000   
15                          Cabbagetown,St. James Town     0.000000   
16                                 Caledonia-Fairbanks     0.000000   
17               Canada Post Gateway Processing Centre     0.000000   
18                                           Cedarbrae     0.000000   
19                                  Central Bay Street     0.012658   
20             Chinatown,Grange Park,Kensington Market     0.000000   
21                                            Christie     0.000000   
22                                Church and Wellesley     0.011628   
23                       Clairlea,Golden Mile,Oakridge     0.000000   
24               Clarks Corners,Sullivan,Tam O'Shanter     0.000000   
25       Cliffcrest,Cliffside,Scarborough Village West     0.000000   
26   Cloverdale,Islington,Martin Grove,Princess Gar...     0.000000   
27                       Commerce Court,Victoria Hotel     0.000000   
28                                          Davisville     0.000000   
29                                    Davisville North     0.000000   
30   Deer Park,Forest Hill SE,Rathnelly,South Hill,...     0.000000   
31         Del Ray,Keelesdale,Mount Dennis,Silverthorn     0.000000   
32             Design Exchange,Toronto Dominion Centre     0.000000   
33                                     Don Mills North     0.000000   
34   Dorset Park,Scarborough Town Centre,Wexford He...     0.000000   
35                         Dovercourt Village,Dufferin     0.000000   
36                                   Downsview Central     0.000000   
37                                 Downsview Northwest     0.000000   
38                                      Downsview West     0.000000   
39                    Downsview,North Park,Upwood Park     0.000000   
40           East Birchmount Park,Ionview,Kennedy Park     0.000000   
41                                        East Toronto     0.000000   
42                                     Emery,Humberlea     0.000000   
43                          Fairview,Henry Farm,Oriole     0.000000   
44               First Canadian Place,Underground city     0.000000   
45                     Flemingdon Park,Don Mills South     0.000000   
46                  Forest Hill North,Forest Hill West     0.000000   
47                                           Glencairn     0.000000   
48                     Guildwood,Morningside,West Hill     0.000000   
49                       Harbord,University of Toronto     0.027778   
50     Harbourfront East,Toronto Islands,Union Station     0.000000   
51                            Harbourfront,Regent Park     0.021277   
52                        High Park,The Junction South     0.000000   
53                Highland Creek,Rouge Hill,Port Union     0.000000   
54                                   Hillcrest Village     0.000000   
55          Humber Bay Shores,Mimico South,New Toronto     0.00000

In [83]:
toronto_grouped.shape

(101, 274)

In [84]:
num_top_venues = 5

for hood in toronto_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = toronto_grouped[toronto_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Adelaide,King,Richmond----
             venue  freq
0      Coffee Shop  0.08
1             Café  0.05
2              Bar  0.04
3  Thai Restaurant  0.03
4           Bakery  0.03


----Agincourt----
                       venue  freq
0  Latin American Restaurant  0.25
1             Clothing Store  0.25
2             Breakfast Spot  0.25
3                     Lounge  0.25
4              Movie Theater  0.00


----Agincourt North,L'Amoreaux East,Milliken,Steeles East----
                       venue  freq
0                 Playground   0.5
1                       Park   0.5
2                Yoga Studio   0.0
3  Middle Eastern Restaurant   0.0
4                      Motel   0.0


----Albion Gardens,Beaumond Heights,Humbergate,Jamestown,Mount Olive,Silverstone,South Steeles,Thistletown----
                  venue  freq
0           Pizza Place  0.14
1         Grocery Store  0.14
2        Sandwich Place  0.14
3  Fast Food Restaurant  0.14
4            Beer Store  0.14


----Alderwood,Long B

In [85]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [86]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = toronto_grouped['Neighborhood']

for ind in np.arange(toronto_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(newyork_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue  \
0                             Adelaide,King,Richmond    Chinese Restaurant   
1                                          Agincourt           Pizza Place   
2  Agincourt North,L'Amoreaux East,Milliken,Steel...           Pizza Place   
3  Albion Gardens,Beaumond Heights,Humbergate,Jam...   American Restaurant   
4                              Alderwood,Long Branch              Bus Stop   

  2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0         Deli / Bodega           Supermarket           Pizza Place   
1          Liquor Store   American Restaurant              Pharmacy   
2   Rental Car Location         Deli / Bodega              Pharmacy   
3         Grocery Store         Boat or Ferry              Bus Stop   
4    Italian Restaurant         Deli / Bodega           Pizza Place   

      5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0                Donut Shop    Spanish Restaurant   Fried Chicken Joint   
1                 Pet Store                 Diner            Restaurant   
2               Coffee Shop              Bus Stop  Fast Food Restaurant   
3             Women's Store   Filipino Restaurant           Event Space   
4  Mediterranean Restaurant            Food Truck        Cosmetics Shop   

  8th Most Common Venue  9th Most Common Venue 10th Most Common Venue  
0           Bus Station            Gas Station   Fast Food Restaurant  
1                  Food           Dance Studio         Cosmetics Shop  
2  Ethiopian Restaurant          Event Service            Event Space  
3               Exhibit             Eye Doctor                Factory  
4    Athletics & Sports  Outdoors & Recreation         Sandwich Place

In [87]:
kclusters = 5

toronto_grouped_clustering = toronto_grouped.drop('Neighborhood', 1)

kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_grouped_clustering)

kmeans.labels_[0:10] 

array([0, 0, 2, 0, 0, 0, 0, 0, 0, 0], dtype=int32)

In [88]:
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

toronto_merged = toronto_data

toronto_merged = toronto_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood', how='right')

toronto_merged.head()

PostalCode           Borough                     Neighborhood   Latitude  \
0        M3A        North York                        Parkwoods  43.753259   
1        M4A        North York                 Victoria Village  43.725882   
2        M5A  Downtown Toronto         Harbourfront,Regent Park  43.654260   
3        M6A        North York  Lawrence Heights,Lawrence Manor  43.718518   
4        M7A      Queen's Park                     Queen's Park  43.662301   

   Longitude  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
0 -79.329656               2          Burger Joint        Sandwich Place   
1 -79.315572               0  Caribbean Restaurant             Juice Bar   
2 -79.360636               0       Harbor / Marina    Seafood Restaurant   
3 -79.464763               0  Gym / Fitness Center   Peruvian Restaurant   
4 -79.389494               0           Coffee Shop                  Park   

  3rd Most Common Venue   4th Most Common Venue 5th Most Common Venue  \
0     French Restaurant             Coffee Shop                   Bar   
1            Donut Shop                    Bank         Grocery Store   
2                  Park  Thrift / Vintage Store                   Bar   
3        Cosmetics Shop                    Park           Coffee Shop   
4        Scenic Lookout               Bookstore                Bakery   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0          Cocktail Bar    Chinese Restaurant  Caribbean Restaurant   
1           Pizza Place           Supermarket            Playground   
2                 Diner     French Restaurant            Smoke Shop   
3         Deli / Bodega              Bus Stop    Athletics & Sports   
4                  Café   American Restaurant            Boxing Gym   

    9th Most Common Venue 10th Most Common Venue  
0     Shanghai Restaurant                 Bakery  
1  Furniture / Home Store               Pharmacy  
2           Boat or Ferry         Baseball Field  
3             Supermarket          Tattoo Parlor  
4                     Gym                    Bar

In [89]:
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

markers_colors = []
for lat, lon, poi, cluster in zip(toronto_merged['Latitude'], toronto_merged['Longitude'], toronto_merged['Neighborhood'], toronto_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [90]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 0, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels       1st Most Common Venue  \
1          North York               0        Caribbean Restaurant   
2    Downtown Toronto               0             Harbor / Marina   
3          North York               0        Gym / Fitness Center   
4        Queen's Park               0                 Coffee Shop   
6         Scarborough               0                        Park   
7          North York               0                       Diner   
8           East York               0                    Pharmacy   
9    Downtown Toronto               0        Fast Food Restaurant   
11          Etobicoke               0           Recreation Center   
12        Scarborough               0        Gym / Fitness Center   
13         North York               0                      Market   
14          East York               0           Indian Restaurant   
15   Downtown Toronto               0                         Bar   
16               York               0                 Pizza Place   
17          Etobicoke               0                        Park   
18        Scarborough               0               Big Box Store   
19       East Toronto               0          Italian Restaurant   
20   Downtown Toronto               0          Italian Restaurant   
22        Scarborough               0                 Yoga Studio   
23          East York               0               Deli / Bodega   
24   Downtown Toronto               0               Deli / Bodega   
25   Downtown Toronto               0                 Pizza Place   
26        Scarborough               0                 Yoga Studio   
27         North York               0               Deli / Bodega   
28         North York               0                   Surf Spot   
29          East York               0  Construction & Landscaping   
30   Downtown Toronto               0          Chinese Restaurant   
31       West Toronto               0                 Yoga Studio   
32        Scarborough               0                 Pizza Place   
33         North York               0                 Coffee Shop   
34         North York               0                 Pizza Place   
36   Downtown Toronto               0          Chinese Restaurant   
37       West Toronto               0            Baseball Stadium   
38        Scarborough               0              Baseball Field   
39         North York               0                         Bar   
41       East Toronto               0               Deli / Bodega   
42   Downtown Toronto               0                 Pizza Place   
43       West Toronto               0          Italian Restaurant   
44        Scarborough               0                 Pizza Place   
45         North York               0                         Bar   
47       East Toronto               0                  Bagel Shop   
48   Downtown Toronto               0                Dance Studio   
49         North York               0                         Bar   
51        Scarborough               0                       Hotel   
54       East Toronto               0                 Supermarket   
55         North York               0          Chinese Restaurant   
56               York               0          Russian Restaurant   
58        Scarborough               0                    Pharmacy   
59         North York               0                 Coffee Shop   
60         North York               0               Moving Target   
63               York               0             Thai Restaurant   
64               York               0                       River   
65        Scarborough               0          Italian Restaurant   
67    Central Toronto               0                       Trail   
69       West Toronto               0                  Donut Shop   
70          Etobicoke               0                 Pizza Place   
71        Scarborough               0          Mexican Restaurant   
72         N

In [91]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 1, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
52  North York               1           Pizza Place                Museum   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
52                  Café           Supermarket                Bakery   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
52            Bagel Shop          Liquor Store           Candy Store   

   9th Most Common Venue 10th Most Common Venue  
52           Coffee Shop     Salon / Barbershop

In [92]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 2, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue  \
0         North York               2          Burger Joint   
10        North York               2    African Restaurant   
21              York               2                 Diner   
35         East York               2  Caribbean Restaurant   
40        North York               2            Donut Shop   
46        North York               2           Pizza Place   
61   Central Toronto               2                Bakery   
66        North York               2     Hotpot Restaurant   
68   Central Toronto               2           Pizza Place   
77         Etobicoke               2           Bus Station   
85       Scarborough               2           Pizza Place   
91  Downtown Toronto               2            Bagel Shop   
98         Etobicoke               2           Pizza Place   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0         Sandwich Place     French Restaurant           Coffee Shop   
10    Chinese Restaurant    Seafood Restaurant                   Bar   
21    Chinese Restaurant    Mexican Restaurant           Pizza Place   
35        Cosmetics Shop                Bakery              Pharmacy   
40         Moving Target   Fried Chicken Joint           Bus Station   
46              Bus Stop              Pharmacy         Deli / Bodega   
61    Italian Restaurant                  Food            Art Museum   
66    Chinese Restaurant   Szechuan Restaurant       Bubble Tea Shop   
68        Hardware Store        Ice Cream Shop        Sandwich Place   
77  Fast Food Restaurant            Restaurant        Mattress Store   
85   Rental Car Location         Deli / Bodega              Pharmacy   
91          Dance Studio                  Park          Burger Joint   
98      Sushi Restaurant    Italian Restaurant                 Diner   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0                    Bar          Cocktail Bar    Chinese Restaurant   
10   American Restaurant     French Restaurant    Salon / Barbershop   
21         Deli / Bodega           Supermarket        Sandwich Place   
35           Flower Shop           Bus Station  Gym / Fitness Center   
40           Supermarket  Fast Food Restaurant    Mexican Restaurant   
46    Chinese Restaurant            Poke Place             Gift Shop   
61         Metro Station        Clothing Store  Caribbean Restaurant   
66                   Spa     Korean Restaurant                   Gym   
68         Tattoo Parlor         Grocery Store            Bagel Shop   
77                  Park         Grocery Store              Pharmacy   
85           Coffee Shop              Bus Stop  Fast Food Restaurant   
91                  Food         Grocery Store           Golf Course   
98              Pharmacy                  Bank  Fast Food Restaurant   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0   Caribbean Restaurant   Shanghai Restaurant                 Bakery  
10               Library             Cafeteria                    Gym  
21            Food Truck                  Park          Train Station  
35    Chinese Restaurant          Liquor Store              Nightclub  
40           Men's Store        Mattress Store   Gym / Fitness Center  
46                  Bank           Coffee Shop         Baseball Field  
61        Sandwich Place              Pharmacy             Donut Shop  
66                Bakery      Asian Restaurant                   Food  
68   Japanese Restaurant                  Bank           Burger Joint  
77           Pizza Place        Discount Store                    Bar  
85  Ethiopian Restaurant         Event Service            Event Space  
91         Women's Store  Fast Food Restaurant            Event Space  
98         Train Station           Coffee Shop             Bagel Shop

In [93]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 3, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue  \
53        North York               3         Deli / Bodega   
57        North York               3       Thai Restaurant   
62   Central Toronto               3            Donut Shop   
101        Etobicoke               3    Mexican Restaurant   

    2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
53          Women's Store   Filipino Restaurant  Ethiopian Restaurant   
57   Caribbean Restaurant              Bus Line                   Gym   
62                   Lake             Hotel Bar           Snack Place   
101         Grocery Store         Train Station           Pizza Place   

    5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
53          Event Service           Event Space               Exhibit   
57          Grocery Store      Asian Restaurant    Chinese Restaurant   
62            Coffee Shop           Pizza Place           Gas Station   
101                Bakery              Bus Stop    Chinese Restaurant   

    8th Most Common Venue        9th Most Common Venue 10th Most Common Venue  
53             Eye Doctor                      Factory     Falafel Restaurant  
57          Women's Store                         Farm          Event Service  
62            Supermarket                          Gym         Ice Cream Shop  
101                  Park  Eastern European Restaurant         Discount Store

In [94]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 4, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
50  North York               4               Theater    Italian Restaurant   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
50  Gym / Fitness Center           Coffee Shop                 Hotel   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
50   American Restaurant                   Gym                   Spa   

   9th Most Common Venue 10th Most Common Venue  
50        Sandwich Place              Wine Shop